# Restaurant Inspections (Delaware)
Mitch Fawcett  November 9, 2023

This is an interactive map showing the results of health inspections of food prep and serving establishments in Delaware


In [1]:
%%capture --no-display  
# Previous line supresses a warning about package versioning

# Load libraries
import pandas as pd   # for dataframe manipulation
import numpy as np  # for numerical analysis
import matplotlib.pyplot as plt   # for generating plots and graphs
from matplotlib.pyplot import figure  # for modifying appearance of plots & graphs
import requests   # to make http post requests to the US Census geocoder
import io  # for working with I/O streams and allow conversion of geocode response to dataframe 
import csv  # reading/writing csv files
import pickle as pk # to store and retrieve dataframes on disk
import csv  # to read text files
import requests # to make http requests for data using census web API
import os   # to list contents of disk drive folders
import sys  # for managing system options
import folium  # the mapping package
from folium import plugins  # to allow cluster markers on maps
import seaborn as sns   # for fancy plotting
from IPython.display import Markdown as md  # for embedding variables in markdown cells
from IPython.display import Image   # to embeg jpg images in notebook
from datetime import datetime

In [2]:
# Settings to improve the display of tabular results
pd.set_option('max_colwidth', 4000)
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
np.set_printoptions(threshold = sys.maxsize)

### IMPORT THE RAW DATASET FROM DELAWARE.GOV

In [3]:
# Import inspection data into a dataframe.  Data  provided by Data.Delaware.Gov Website
# https://data.delaware.gov/Health/Restaurant-Inspection-Violations/384s-wygj

inspections_df = pd.read_table('Restaurant_Inspection_Violations_20231105.tsv', delimiter = '\t')

# Replaces spaces with '_' in column names
inspections_df.columns = [c.replace(' ', '_') for c in inspections_df.columns]

# Convert the inspection date to a real date value so they can be sorted later
inspections_df['Inspection_Date']= pd.to_datetime(inspections_df['Inspection_Date'])

In [4]:
# Inspect the raw data
inspections_df.head()

Food_Establishment_Name Food_Establishment_Street_Address  \
0  1 In Town African Restaurant      240 S Dupont Hwy Suite # 300   
1             1000 Degree Pizza         4526 New Linden Hill Road   
2             1000 Degree Pizza         4526 New Linden Hill Road   
3             1000 Degree Pizza         4526 New Linden Hill Road   
4             1000 Degree Pizza         4526 New Linden Hill Road   

  Food_Establishment_City  Food_Establishment_Zip_Code Inspection_Date  \
0              New Castle                      19720.0      2022-03-04   
1              Wilmington                      19808.0      2022-07-08   
2              Wilmington                      19808.0      2022-07-08   
3              Wilmington                      19808.0      2022-07-08   
4              Wilmington                      19808.0      2022-07-08   

  Inspection_Type Violation_Code  \
0         Routine            NaN   
1         Routine       2-102.12   
2         Routine       5-202.12   
3         Routine       6-301.12   
4         Routine       3-501.16   

                                            Violation_Description  \
0                                                             NaN   
1                               Certified Food Protection Manager   
2                                 Handwashing Sinks, Installation   
3                                           Hand Drying Provision   
4  Time/Temperature Control for Safety Food, Hot and Cold Holding   

                                                                   Geocoded_Location  
0  240 S Dupont Hwy Suite # 300\nNew Castle, DE 19720\n(39.653333979, -75.616564004)  
1     4526 New Linden Hill Road\nWilmington, DE 19808\n(39.737731167, -75.690144456)  
2     4526 New Linden Hill Road\nWilmington, DE 19808\n(39.737731167, -75.690144456)  
3     4526 New Linden Hill Road\nWilmington, DE 19808\n(39.737731167, -75.690144456)  
4     4526 New Linden Hill Road\nWilmington, DE 19808\n(39.737731167, -75.690144456)

### CREATE COLUMNS FOR LONGITUDE & LATITUDE OF ESTABLISHMENTS

In [5]:
# Locations will be mapped using the longitude/latitude values in the 'Geocoded_Location column'.
# These numbers need to be extracted out of Geocoded_Location and added as a new column.

# Split the Geocoded_Location column on newline character \n
coordinates_df = inspections_df.Geocoded_Location.str.split(pat="\n", expand=True)

# Give the cooridnates column a better name than '2'
coordinates_df.rename(columns={0:'col_1', 1:'col_2', 2:'Lat_Long'},inplace=True)

# Inspect the result
coordinates_df["Lat_Long"].head()

0    (39.653333979, -75.616564004)
1    (39.737731167, -75.690144456)
2    (39.737731167, -75.690144456)
3    (39.737731167, -75.690144456)
4    (39.737731167, -75.690144456)
Name: Lat_Long, dtype: object

In [6]:
# Add it as another column to the dataset
inspections_df['Lat_Long'] = coordinates_df["Lat_Long"]

In [7]:
# Separate the cooordinate pairs into two columns for Longitude and Latitude
inspections_df[['Latitude', 'Longitude']] = inspections_df['Lat_Long'].str.rsplit(', ', expand=True)

# Get rid of '(' and ')' characters in the new columns
inspections_df['Latitude'] = inspections_df['Latitude'].str.replace('(','')
inspections_df['Longitude'] = inspections_df['Longitude'].str.replace(')','')

In [8]:
# Inspect the data now has a dedicated column for coordinates
inspections_df.head()

Food_Establishment_Name Food_Establishment_Street_Address  \
0  1 In Town African Restaurant      240 S Dupont Hwy Suite # 300   
1             1000 Degree Pizza         4526 New Linden Hill Road   
2             1000 Degree Pizza         4526 New Linden Hill Road   
3             1000 Degree Pizza         4526 New Linden Hill Road   
4             1000 Degree Pizza         4526 New Linden Hill Road   

  Food_Establishment_City  Food_Establishment_Zip_Code Inspection_Date  \
0              New Castle                      19720.0      2022-03-04   
1              Wilmington                      19808.0      2022-07-08   
2              Wilmington                      19808.0      2022-07-08   
3              Wilmington                      19808.0      2022-07-08   
4              Wilmington                      19808.0      2022-07-08   

  Inspection_Type Violation_Code  \
0         Routine            NaN   
1         Routine       2-102.12   
2         Routine       5-202.12   
3         Routine       6-301.12   
4         Routine       3-501.16   

                                            Violation_Description  \
0                                                             NaN   
1                               Certified Food Protection Manager   
2                                 Handwashing Sinks, Installation   
3                                           Hand Drying Provision   
4  Time/Temperature Control for Safety Food, Hot and Cold Holding   

                                                                   Geocoded_Location  \
0  240 S Dupont Hwy Suite # 300\nNew Castle, DE 19720\n(39.653333979, -75.616564004)   
1     4526 New Linden Hill Road\nWilmington, DE 19808\n(39.737731167, -75.690144456)   
2     4526 New Linden Hill Road\nWilmington, DE 19808\n(39.737731167, -75.690144456)   
3     4526 New Linden Hill Road\nWilmington, DE 19808\n(39.737731167, -75.690144456)   
4     4526 New Linden Hill Road\nWilmington, DE 19808\n(39.737731167, -75.690144456)   

                        Lat_Long      Latitude      Longitude  
0  (39.653333979, -75.616564004)  39.653333979  -75.616564004  
1  (39.737731167, -75.690144456)  39.737731167  -75.690144456  
2  (39.737731167, -75.690144456)  39.737731167  -75.690144456  
3  (39.737731167, -75.690144456)  39.737731167  -75.690144456  
4  (39.737731167, -75.690144456)  39.737731167  -75.690144456

### PREPARE A LIST OF ESTABLISHMENT NAMES AND LOCATIONS

In [9]:
# Create a dataframe that contains a unique list of food establishment names and coordinates.
# Location values repeat in the dataset for each inspection & violation.  Need to get the
# unique values so only one marker is added to the map for each food establishment.
unique_locations_df = inspections_df[['Food_Establishment_Name', 'Latitude', 'Longitude']].drop_duplicates()

In [10]:
# Review some results
unique_locations_df.head()

Food_Establishment_Name      Latitude      Longitude
0   1 In Town African Restaurant  39.653333979  -75.616564004
1              1000 Degree Pizza  39.737731167  -75.690144456
8                         11-Jul  39.178200014  -75.527233032
11                      13 Wingz  38.645889987  -75.625000976
15         1300 Bar & Restaurant  39.748308989  -75.545611026

### COUNT NUMBER OF VIOLATIONS FOR EACH INSPECTION

In [11]:
# Create a dataset that has the count of violations for each inspection
location_inspection_df = inspections_df[['Food_Establishment_Name', 'Inspection_Date', 'Violation_Code']].drop_duplicates()
grouped_df = location_inspection_df.groupby(['Food_Establishment_Name', 'Inspection_Date'])
inspection_violation_counts_df = grouped_df.count()

# Make the Food_Establishment_Name and Inspection_Date columns regular columns, not indexes
inspection_violation_counts_df = inspection_violation_counts_df.reset_index()

# Change a column name
inspection_violation_counts_df.rename(columns = {'Violation_Code': 'Violation_Count'}, inplace = True)


In [12]:
inspection_violation_counts_df.head()

Food_Establishment_Name Inspection_Date  Violation_Count
0  1 In Town African Restaurant      2022-03-04                0
1             1000 Degree Pizza      2022-07-08                5
2             1000 Degree Pizza      2022-08-01                1
3             1000 Degree Pizza      2022-08-11                0
4                        11-Jul      2021-11-18                1

### COUNT NUMBER OF INSPECTIONS FOR EACH ESTABLISHMENT

In [13]:
# Count rows in prior result grouping by establishment name to get the count of inspection dates
establishment_inspection_counts_df = inspection_violation_counts_df.groupby(['Food_Establishment_Name']).count().reset_index()
establishment_inspection_counts_df.rename(columns = {'Inspection_Date': 'Inspection_Count'}, inplace = True)
establishment_inspection_counts_df = establishment_inspection_counts_df.drop(columns=['Violation_Count'])


In [14]:
establishment_inspection_counts_df.head(10)

Food_Establishment_Name  Inspection_Count
0  1 In Town African Restaurant                 1
1             1000 Degree Pizza                 3
2                        11-Jul                 2
3                      13 Wingz                 2
4         1300 Bar & Restaurant                 7
5                 14 Global LLC                 2
6               1776 Restaurant                 2
7            1857 Jackson House                 3
8                          1861                 2
9           2 Angel's Ice Cream                 3

### TOTAL NUMBER OF VIOLATIONS FOR EACH ESTABLISHMENT

In [15]:
# Use previous result to calculate the total number of violations for each establishment
establishment_violation_counts_df = inspection_violation_counts_df.groupby(['Food_Establishment_Name'])['Violation_Count'].sum().reset_index()

establishment_violation_counts_df.rename(columns = {'Violation_Count': 'Total_Violation_Count'}, inplace = True)

In [16]:
establishment_violation_counts_df.head()

Food_Establishment_Name  Total_Violation_Count
0  1 In Town African Restaurant                      0
1             1000 Degree Pizza                      6
2                        11-Jul                      3
3                      13 Wingz                      3
4         1300 Bar & Restaurant                     25

### GET THE DATE OF THE MOST RECENT INSPECTION FOR EACH ESTABLISHMENT

In [17]:
# Find the most recent inspection date for each establishment

# Get a list of all inspection dates for each estalishment
inspection_dates_df = inspections_df[['Food_Establishment_Name', 'Inspection_Date']].drop_duplicates()

# Get the most recent inspection date for each place.
latest_inspection_date_df = inspection_dates_df.loc[inspection_dates_df
        .groupby('Food_Establishment_Name').Inspection_Date.idxmax()]

# Change the date column name
latest_inspection_date_df.rename(columns = {'Inspection_Date': 'Latest_Inspection_Date'}, inplace = True)

In [18]:
latest_inspection_date_df.head()

Food_Establishment_Name Latest_Inspection_Date
0   1 In Town African Restaurant             2022-03-04
7              1000 Degree Pizza             2022-08-11
9                         11-Jul             2023-05-26
12                      13 Wingz             2023-02-08
36         1300 Bar & Restaurant             2023-08-10

### NUMBER OF VIOLATIONS IN THE MOST RECENT INSPECTION FOR EACH ESTABLISHMENT

In [19]:
latest_inspection_violations_df = latest_inspection_date_df.merge(
    inspection_violation_counts_df,
    left_on=['Latest_Inspection_Date', 'Food_Establishment_Name'],
    right_on=['Inspection_Date', 'Food_Establishment_Name'],
    how='inner')

In [20]:
latest_inspection_violations_df.head(10)

Food_Establishment_Name Latest_Inspection_Date Inspection_Date  \
0  1 In Town African Restaurant             2022-03-04      2022-03-04   
1             1000 Degree Pizza             2022-08-11      2022-08-11   
2                        11-Jul             2023-05-26      2023-05-26   
3                      13 Wingz             2023-02-08      2023-02-08   
4         1300 Bar & Restaurant             2023-08-10      2023-08-10   
5                 14 Global LLC             2023-09-01      2023-09-01   
6               1776 Restaurant             2022-08-31      2022-08-31   
7            1857 Jackson House             2023-08-10      2023-08-10   
8                          1861             2023-02-10      2023-02-10   
9           2 Angel's Ice Cream             2022-07-20      2022-07-20   

   Violation_Count  
0                0  
1                0  
2                2  
3                3  
4                4  
5                2  
6                5  
7                2  
8                1  
9                2

### IDENTIFY ESTABLISHMENTS THAT HAD NO VIOLATIONS IN THEIR LATEST INSPECTION

In [21]:
# Find places that had no violations on most recent inspection.
latest_inspection_no_violations_df = latest_inspection_violations_df.loc[latest_inspection_violations_df['Violation_Count'] == 0]    


In [22]:
latest_inspection_no_violations_df

Food_Establishment_Name  \
0                           1 In Town African Restaurant   
1                                      1000 Degree Pizza   
11                                      2S Pizza Company   
12                                           2nd To None   
13                                  3 Countries Pizzeria   
22                                 7 Eleven Store #36871   
23                                       7*eleven 11301d   
25                                        7-Eleven #1578   
26                                      7-Eleven #41263A   
28                                       7-Eleven 20027K   
33                                       7-eleven #33102   
34                                      7-eleven #40122h   
35                                       7-eleven 11284c   
36                                        7-eleven 1635f   
37                                       7-eleven 33102b   
38                                       7-eleven 33102j   
41                                7-eleven Store #36871a   
42                                 7-eleven Store 34751a   
46                               99 Sea Level Restaurant   
48     A I Dupont Hospital For Children- Caf+�/einsteins   
49      A I Dupont Hospital For Children- CafT/einsteins   
52                                  A and R's Food To Go   
54                                          AAA Deli Inc   
57                                                ATER'S   
60             Aaa - Mid Atlantic - New Operation Center   
62                         Abessinio Stadium Concessions   
67               Academia Antonia Alsonso Charter School   
69                                        Acai You Again   
73                                      Acme 2680-newark   
76                               Acme Market Store #7806   
78                               Acme Market Store #7817   
86                                       Addictive Tacos   
90                                    Afc Sushi @ U Of D   
97                              Aha South Indian Cuisine   
100                                         Akwaaba Eats   
103                     Albert H Jones Ele Sch Cafeteria   
104                                  Alberta's Soul Food   
106                                      Aldergate U M C   
110                              Alfredo's Pizza Gallery   
111               Ali Baba Middle Eastern Restaurant Inc   
112                                             All Blue   
115                                        Amato's Pizza   
118                             American Legion Post #19   
121                               American Legion Post 5   
135                                     Angie's Lonchera   
136              Angola By The Bay Property Owners Assoc   
140                            Anthony's Taqueria Mobile   
141                                   Antioch Ame Church   
146                 Appoquinimink Early Childhood Center   
151                                      Aquinas Academy   
152                                               Arby's   
153                                    Arby's Georgetown   
154                                    Arby's RT10 Dover   
156                                     Arby'srestaurant   
157                                     Arbys Restaurant   
163                                          Arena's Pub   
166                               Arianna's Mexican Food   
168                                            Army of 2   
173                       Ashland Nature-overnight Lodge   
178                           Aspira Academy High School   
186                                       Augusta Grille   
187                                        Augustine Inn   
188                   Augustine Inn Seafood & Chop House   
191              Aunt Patti's Philly Cheese Steaks (MOB)   
193                                        Auntie Anne's   
196                                    Auntie Anne's MOB   
204          

### CREATE SOME FUNCTIONS TO SET MAP MARKER APPEARANCE

In [23]:
# Create a function that sets a marker icon based on inspection results
# If the establishment had no violations in its most recent inspection, use "smile" icon,
# Otherwise use 'frown'
def get_status_icon(location_name):
    if location_name in latest_inspection_no_violations_df['Food_Establishment_Name'].values:
        return 'smile'
    else:
        return 'frown'

In [24]:
# Create a function that retuns the most recent inspection date
def get_latest_inspection_date(location_name):
    latest_date_df = latest_inspection_date_df.loc[latest_inspection_date_df['Food_Establishment_Name'] == location_name]
    return str(latest_date_df['Latest_Inspection_Date'].item())[:10] 



In [25]:
# Create a function that returns the total number of inspections for the establishment
def inspection_count(location_name):
    try:
        inspect_count_df = establishment_inspection_counts_df.loc[establishment_inspection_counts_df['Food_Establishment_Name'] == location_name]    
        return str(inspect_count_df['Inspection_Count'].item())
    except:
        return 'unknown'

In [26]:
# Create a function that returns the number of violations to-date for the establishment
def violations_total(location_name):
    try:
        violation_count_df = establishment_violation_counts_df.loc[establishment_violation_counts_df['Food_Establishment_Name'] == location_name]    
        return str(violation_count_df['Total_Violation_Count'].item())
    except:
        return 'unknown'


In [27]:
# Create a function that returns the number of violations from the most recent inspection 
# for the establishment
def violations_recent(location_name):
    try:
        violation_count_df = latest_inspection_violations_df.loc[latest_inspection_violations_df['Food_Establishment_Name'] == location_name]    
        return str(violation_count_df['Violation_Count'].item())
    except:
        return 'unknown'

In [28]:
# Start a map of Delaware centered on Dover
# 39.1582°, -75.5244°  # coordinates of Dover, DE
# 39.620198 -75.670477  # coordinates of Bear, DE
mp = folium.Map(location=[39.620198, -75.670477], zoom_start=14, width=900, height=550, control_scale=True)
# mp is the map object.  I will next add a marker to it for each food location.

In [29]:
# Add the markers to the map
for index, row in unique_locations_df.iterrows():
    # print(row['Food_Establishment_Name'],row['Latitude'], row['Longitude'])
    # Get status icon
    icon_name = get_status_icon(row['Food_Establishment_Name'])
    total_inspections = inspection_count(row['Food_Establishment_Name'])
    total_violations = violations_total(row['Food_Establishment_Name'])
    recent_violations = violations_recent(row['Food_Establishment_Name'])
    latest_inspection_date = get_latest_inspection_date(row['Food_Establishment_Name'])
    location_name = row['Food_Establishment_Name']
    try:
        folium.Marker(
            location = [row['Latitude'], row['Longitude']],
            popup = row['Food_Establishment_Name'],
            icon = folium.Icon(color = 'blue', 
                               icon_color = 'yellow', 
                               icon = icon_name, 
                               prefix = 'fa'),
            tooltip = location_name[0:20]
            + '<br>' + 'Number of inspections: ' + str(total_inspections)
            + '<br>' + 'Latest inspection date: ' + str(latest_inspection_date)
            + '<br>' + 'Total violations: ' + str(total_violations)
            + '<br>' + 'Recent violations; ' + str(recent_violations)
        ).add_to(mp)
    except: # not all locations are geocoded in the dataset, skip them
        print(row['Food_Establishment_Name'], ' No coordinates available')
        pass

Aspira Academy High School  No coordinates available
Eat BAP Mobile Unit  No coordinates available
Newark Charter School  No coordinates available


In [30]:
# Display the map
mp